In [1]:
import librosa
import numpy as np
import IPython.display as idisplay
import matplotlib.pyplot as plt

In [6]:
audio, sr = librosa.load("input_olp.wav", sr=None, mono=False)
audio = audio.reshape(1,-1)
channels, og_len = audio.shape
print(audio.shape, sr)
idisplay.display(idisplay.Audio(waveform, rate=sr))
idisplay.display(idisplay.Audio(waveform, rate=sr * 2))

(1, 475136) 48000


In [20]:
win_len = 5000 
win_f = np.hanning(win_len)
anls_hop_len = 2000 
scaling = 2 ** (5 / 12)   #pitch shift
synth_hop_len = int(anls_hop_len * scaling)

new_waveform_len = int(np.ceil(og_len / anls_hop_len) * synth_hop_len) + win_len
new_waveform = np.zeros((channels, new_waveform_len)) 
norm_new_waveform = np.zeros((channels, new_waveform_len))
new_scales = np.zeros(new_waveform_len)

# loop through windows
last_idx = 0
for i in range(0, og_len, anls_hop_len):
    #select a window from the orginal waveform
    clipped_len = min(win_len, og_len - i)
    window = audio[:, i:i + clipped_len] * win_f[None, :clipped_len] #window multiplied by windowing function

    idx = int(i * scaling)    # index of synthesized waveform
    # search for good synthesis window placement
    if idx > 0:
        idx = max(0, idx - 500)
        overlap = max(0, min(win_len - idx + last_idx, new_waveform_len - idx, window.shape[1]))
        min_area = float("inf")
        for j in range(idx, min(idx + 1000, new_waveform_len - clipped_len, idx + overlap)):
            # area = np.sum(np.abs(window[:, :overlap] - norm_new_waveform[:, j:j + overlap])) / overlap
            area = -np.sum(window[:, :overlap] * norm_new_waveform[:, j:j + overlap])
            if area < min_area:
                min_area = area
                idx = j
            overlap -= 1
            if not overlap: break

    # add window to new waveform
    window_waveform = new_waveform[:, idx:idx + clipped_len]
    window_waveform += window
    # add up windowing weights for normalization
    window_scales = new_scales[idx:idx + clipped_len]
    window_scales += win_f[:clipped_len]
    norm_new_waveform[:, idx:idx + clipped_len] = window_waveform / np.where(window_scales == 0, 1, window_scales)

    last_idx = idx

new_waveform = norm_new_waveform

idisplay.display(idisplay.Audio(new_waveform, rate=sr * scaling))

In [18]:
new_waveform[0].shape

(361524,)

In [19]:
from scipy.io.wavfile import write

duration = 10  # seconds
new_sr = int(sr*scaling)

# Specify the output WAV file path
output_file = "pitch_down_sola.wav"

# Write the WAV file
write(output_file, new_sr, new_waveform[0])